<a href="https://colab.research.google.com/github/joevincentgaltie/OODDetection_ENSAE/blob/main/Retrieve_Hidden_States.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!pip install datasets
!pip install transformers
!pip install todd

In [15]:
pip install evaluate

Defaulting to user installation because normal site-packages is not writeable
You should consider upgrading via the '/Library/Developer/CommandLineTools/usr/bin/python3 -m pip install --upgrade pip' command.
Note: you may need to restart the kernel to use updated packages.


In [2]:
import pandas as pd 
import numpy as np 

from tqdm import tqdm
import datasets
from datasets import load_dataset

import nltk
from nltk.tokenize import TreebankWordTokenizer
nltk.download('punkt')
sent_detector = nltk.data.load('tokenizers/punkt/english.pickle')
nltk.download('stopwords')
from nltk.corpus import stopwords
from gensim.models.phrases import Phrases, Phraser

import torch
from torch.utils.data import DataLoader, TensorDataset
from torch.optim import AdamW

from transformers import AutoTokenizer, BertForSequenceClassification, get_scheduler, AutoModelForSequenceClassification
#from pytorch_transformers import WarmupLinearSchedule

[nltk_data] Downloading package punkt to
[nltk_data]     /Users/joevincentgaltie/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/joevincentgaltie/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [51]:
SST2Dataset = load_dataset('glue','sst2')
SST2Dataset = SST2Dataset.rename_column('sentence', 'text')
SST2Dataset = SST2Dataset.remove_columns('idx')
train_dataloader = DataLoader(SST2Dataset['train'], batch_size=8)

Found cached dataset glue (/Users/joevincentgaltie/.cache/huggingface/datasets/glue/sst2/1.0.0/dacbe3125aa31d7f70367a07a8a9e72a5a0bfeb5fc42e75c9db75b96da6053ad)


  0%|          | 0/3 [00:00<?, ?it/s]

In [52]:
tokenizer = AutoTokenizer.from_pretrained("echarlaix/bert-base-uncased-sst2-acc91.1-d37-hybrid")
model = AutoModelForSequenceClassification.from_pretrained("echarlaix/bert-base-uncased-sst2-acc91.1-d37-hybrid", output_hidden_states=True)

In [53]:
if torch.cuda.is_available():
  device = 'cuda'
  print('DEVICE = ', torch.cuda.get_device_name(0))
else:
  device = 'cpu'
  print('DEVICE = ', 'CPU')
model = model.to(device)

DEVICE =  CPU


In [123]:
# test de récupérer hidden states pour un seul batch
for batch in tqdm(train_dataloader):
        #batch = {k: v.to(device) for k, v in batch.items()}
        inputs = tokenizer(batch['text'], return_tensors="pt", truncation=True, padding=True)['input_ids'].to(device)
        outputs = model(inputs)
        print(outputs.hidden_states[0].size())
        #break

print(outputs)

  0%|          | 2/8419 [00:00<22:30,  6.23it/s]

torch.Size([8, 29, 768])
torch.Size([8, 23, 768])


  0%|          | 4/8419 [00:00<25:22,  5.53it/s]

torch.Size([8, 34, 768])
torch.Size([8, 26, 768])


  0%|          | 6/8419 [00:01<28:24,  4.94it/s]

...

  1%|          | 64/8419 [00:11<23:07,  6.02it/s]

torch.Size([8, 35, 768])
torch.Size([8, 20, 768])


  1%|          | 65/8419 [00:12<26:04,  5.34it/s]

torch.Size([8, 42, 768])


KeyboardInterrupt: 

In [118]:
for i in train_dataloader : 
    print(i)

{'text': ['hide new secretions from the parental units ', 'contains no wit , only labored gags ', 'that loves its characters and communicates something rather beautiful about human nature ', 'remains utterly satisfied to remain the same throughout ', 'on the worst revenge-of-the-nerds clichés the filmmakers could dredge up ', "that 's far too tragic to merit such superficial treatment ", 'demonstrates that the director of such hollywood blockbusters as patriot games can still turn out a small , personal film with an emotional wallop . ', 'of saucy '], 'label': tensor([0, 0, 1, 0, 0, 0, 1, 1])}
{'text': ["a depressed fifteen-year-old 's suicidal poetry ", "are more deeply thought through than in most ` right-thinking ' films ", 'goes to absurd lengths ', "for those moviegoers who complain that ` they do n't make movies like they used to anymore ", "the part where nothing 's happening , ", 'saw how bad this movie was ', 'lend some dignity to a dumb story ', 'the greatest musicians '], 'l

In [55]:
outputs.hidden_states[0].shape[0]

8

In [56]:
print(f'there are {len(outputs.hidden_states)} hidden layers')
print(f'batches are composed of {outputs.hidden_states[0].shape[0]} sentences')
print(f'sentences are composed of max {outputs.hidden_states[0].shape[1]} tokens ?')
print(f'each token is embedded in {outputs.hidden_states[0].shape[2]} dimensions')

there are 13 hidden layers
batches are composed of 8 sentences
sentences are composed of max 29 tokens ?
each token is embedded in 768 dimensions


In [78]:
outputs.hidden_states

(tensor([[[ 1.5597e-01, -2.6601e-01, -3.1719e-01,  ..., -4.8019e-03,
            1.4476e-02,  1.5220e-01],
          [ 4.7814e-02, -1.2341e+00, -7.6091e-03,  ...,  7.8239e-01,
           -4.6695e-01,  5.2692e-01],
          [-1.7656e-01, -5.6073e-02,  5.1213e-01,  ..., -6.1686e-01,
            2.9974e-01, -1.2658e+00],
          ...,
          [-1.0055e-01, -3.6420e-01, -3.5219e-02,  ..., -1.3968e-01,
           -1.1397e-01,  1.0760e-02],
          [-4.5789e-02, -4.8162e-01, -4.4026e-02,  ..., -3.1198e-01,
           -2.2934e-01, -4.9327e-02],
          [ 5.6678e-02, -3.4025e-01,  8.7591e-02,  ...,  1.2868e-04,
           -3.9694e-01, -7.2258e-02]],
 
         [[ 1.5597e-01, -2.6601e-01, -3.1719e-01,  ..., -4.8019e-03,
            1.4476e-02,  1.5220e-01],
          [ 4.2895e-01,  9.7244e-02,  3.0032e-01,  ...,  8.3743e-01,
           -1.3315e-01,  7.8043e-02],
          [-7.7761e-01,  6.6188e-01,  3.4857e-02,  ..., -6.0394e-01,
           -1.3760e-01, -8.8711e-02],
          ...,
    

In [91]:
outputs.hidden_states[0].size()

torch.Size([8, 29, 768])

In [106]:
list_of_tensors = [torch.empty(8, 512, 768) for _ in range(13)]

def hidden_states_collection (list_of_tensors, outputs, test=False):
  hidden_states = outputs.hidden_states
  for i, ele  in enumerate(outputs.hidden_states): 
    tuple_of_tensors[i]=torch.cat((tuple_of_tensors[i],ele))
 
  return list_of_tensors

hidden_states_collection(list_of_tensors, outputs, test=False)

[tensor([[[0., 0., 0.,  ..., 0., 0., 0.],
          [0., 0., 0.,  ..., 0., 0., 0.],
          [0., 0., 0.,  ..., 0., 0., 0.],
          ...,
          [0., 0., 0.,  ..., 0., 0., 0.],
          [0., 0., 0.,  ..., 0., 0., 0.],
          [0., 0., 0.,  ..., 0., 0., 0.]],
 
         [[0., 0., 0.,  ..., 0., 0., 0.],
          [0., 0., 0.,  ..., 0., 0., 0.],
          [0., 0., 0.,  ..., 0., 0., 0.],
          ...,
          [0., 0., 0.,  ..., 0., 0., 0.],
          [0., 0., 0.,  ..., 0., 0., 0.],
          [0., 0., 0.,  ..., 0., 0., 0.]],
 
         [[0., 0., 0.,  ..., 0., 0., 0.],
          [0., 0., 0.,  ..., 0., 0., 0.],
          [0., 0., 0.,  ..., 0., 0., 0.],
          ...,
          [0., 0., 0.,  ..., 0., 0., 0.],
          [0., 0., 0.,  ..., 0., 0., 0.],
          [0., 0., 0.,  ..., 0., 0., 0.]],
 
         ...,
 
         [[0., 0., 0.,  ..., 0., 0., 0.],
          [0., 0., 0.,  ..., 0., 0., 0.],
          [0., 0., 0.,  ..., 0., 0., 0.],
          ...,
          [0., 0., 0.,  ..., 0., 

In [110]:
list_of_tensors = [torch.empty(8, 29, 768) for _ in range(13)]

for batch in train_dataloader:
        inputs = tokenizer(batch['text'], return_tensors="pt", truncation=True, padding=True)['input_ids'].to(device)
        outputs = model(inputs)
        list_of_tensors = hidden_states_collection (list_of_tensors, outputs, test=False)
 

RuntimeError: Sizes of tensors must match except in dimension 0. Expected size 29 but got size 23 for tensor number 1 in the list.

In [105]:
for ele, i  in enumerate(outputs.hidden_states): 
    print(ele,i)

0 tensor([[[ 1.5597e-01, -2.6601e-01, -3.1719e-01,  ..., -4.8019e-03,
           1.4476e-02,  1.5220e-01],
         [ 4.7814e-02, -1.2341e+00, -7.6091e-03,  ...,  7.8239e-01,
          -4.6695e-01,  5.2692e-01],
         [-1.7656e-01, -5.6073e-02,  5.1213e-01,  ..., -6.1686e-01,
           2.9974e-01, -1.2658e+00],
         ...,
         [-1.0055e-01, -3.6420e-01, -3.5219e-02,  ..., -1.3968e-01,
          -1.1397e-01,  1.0760e-02],
         [-4.5789e-02, -4.8162e-01, -4.4026e-02,  ..., -3.1198e-01,
          -2.2934e-01, -4.9327e-02],
         [ 5.6678e-02, -3.4025e-01,  8.7591e-02,  ...,  1.2868e-04,
          -3.9694e-01, -7.2258e-02]],

        [[ 1.5597e-01, -2.6601e-01, -3.1719e-01,  ..., -4.8019e-03,
           1.4476e-02,  1.5220e-01],
         [ 4.2895e-01,  9.7244e-02,  3.0032e-01,  ...,  8.3743e-01,
          -1.3315e-01,  7.8043e-02],
         [-7.7761e-01,  6.6188e-01,  3.4857e-02,  ..., -6.0394e-01,
          -1.3760e-01, -8.8711e-02],
         ...,
         [-1.0055e-01, 

In [104]:
for i, v in zip(tuple_of_tensors, outputs.hidden_states) :
    print(i.size(),v.size(),torch.cat((i,v),0).size())

torch.Size([8, 29, 768]) torch.Size([8, 29, 768]) torch.Size([16, 29, 768])
torch.Size([8, 29, 768]) torch.Size([8, 29, 768]) torch.Size([16, 29, 768])
torch.Size([8, 29, 768]) torch.Size([8, 29, 768]) torch.Size([16, 29, 768])
torch.Size([8, 29, 768]) torch.Size([8, 29, 768]) torch.Size([16, 29, 768])
torch.Size([8, 29, 768]) torch.Size([8, 29, 768]) torch.Size([16, 29, 768])
torch.Size([8, 29, 768]) torch.Size([8, 29, 768]) torch.Size([16, 29, 768])
torch.Size([8, 29, 768]) torch.Size([8, 29, 768]) torch.Size([16, 29, 768])
torch.Size([8, 29, 768]) torch.Size([8, 29, 768]) torch.Size([16, 29, 768])
torch.Size([8, 29, 768]) torch.Size([8, 29, 768]) torch.Size([16, 29, 768])
torch.Size([8, 29, 768]) torch.Size([8, 29, 768]) torch.Size([16, 29, 768])
torch.Size([8, 29, 768]) torch.Size([8, 29, 768]) torch.Size([16, 29, 768])
torch.Size([8, 29, 768]) torch.Size([8, 29, 768]) torch.Size([16, 29, 768])
torch.Size([8, 29, 768]) torch.Size([8, 29, 768]) torch.Size([16, 29, 768])


### Scoring first try

In [41]:
pip install Todd

Defaulting to user installation because normal site-packages is not writeable
You should consider upgrading via the '/Library/Developer/CommandLineTools/usr/bin/python3 -m pip install --upgrade pip' command.
Note: you may need to restart the kernel to use updated packages.


In [42]:
import Todd

In [43]:
help(Todd)

Help on package Todd:

NAME
    Todd

PACKAGE CONTENTS
    basescorers
    datadepths
    featuresscorers
    filters
    itscorers
    query_based_scorers (package)
    utils (package)

FILE
    (built-in)




In [73]:
import Todd.basescorers
import Todd.featuresscores
import Todd.datadepts

In [74]:
import Todd

In [47]:
import T

from Todd.featuresscorers import (
    #ScorerType, 
    MahalanobisScorer, 
    CosineProjectionScorer, 
    DataDepthScorer, 
)

~ScorerType

In [70]:
MahalanobisScorer(outputs.hidden_states[-1]).accumulate()

TypeError: accumulate() missing 1 required positional argument: 'output'

In [28]:
todd.info

AttributeError: ignored

In [ ]:
# pour voir chaque couche
model.bert.encoder.layer

ModuleList(
  (0): BertLayer(
    (attention): BertAttention(
      (self): BertSelfAttention(
        (query): Linear(in_features=768, out_features=320, bias=True)
        (key): Linear(in_features=768, out_features=320, bias=True)
        (value): Linear(in_features=768, out_features=320, bias=True)
        (dropout): Dropout(p=0.1, inplace=False)
      )
      (output): BertSelfOutput(
        (dense): Linear(in_features=320, out_features=768, bias=True)
        (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
        (dropout): Dropout(p=0.1, inplace=False)
      )
    )
    (intermediate): BertIntermediate(
      (dense): Linear(in_features=768, out_features=3072, bias=True)
      (intermediate_act_fn): GELUActivation()
    )
    (output): BertOutput(
      (dense): Linear(in_features=3072, out_features=768, bias=True)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
  )
  (1): BertLayer

In [72]:
layer_selection = {"last": [-1], "all": [l for l in range(13)]}

detectors: List[ScorerType] = [
    MahalanobisScorer(layers=layer_selection["last"]), 
    CosineProjectionScorer(layers=layer_selection["all"]), 
    # DataDepthScorer(layers=layer_selection["all"])
]

detector_names = [detector.__class__.__name__ for detector in detectors]

NameError: name 'List' is not defined

In [77]:
MahalanobisScorer.__dict__

mappingproxy({'__module__': 'Todd.featuresscorers',
              '__doc__': '\n    Filters a batch of outputs based on the Mahalanobis distance of the first sequence returned for each input.\n    ',
              '__init__': <function Todd.featuresscorers.MahalanobisScorer.__init__(self, layers: List[int] = (-1,), **kwargs)>,
              'accumulate': <function Todd.featuresscorers.MahalanobisScorer.accumulate(self, output: transformers.utils.generic.ModelOutput, y: Optional[List[int]] = None) -> None>,
              'fit': <function Todd.featuresscorers.MahalanobisScorer.fit(self, per_layer_embeddings: Optional[Dict[Tuple[int, int], List[torch.Tensor]]] = None, **kwargs)>,
              'dump_scorer': <function Todd.featuresscorers.MahalanobisScorer.dump_scorer(self, path: pathlib.Path)>,
              'load_scorer': <function Todd.featuresscorers.MahalanobisScorer.load_scorer(self, path: pathlib.Path)>,
              'compute_per_layer_per_class_distances': <function Todd.features

In [6]:
import Todd
import toddbenchmark

In [14]:
pip install evaluate

Defaulting to user installation because normal site-packages is not writeable
     |████████████████████████████████| 81 kB 3.5 MB/s eta 0:00:01
  Consider adding this directory to PATH or, if you prefer to suppress this warning, use --no-warn-script-location.
You should consider upgrading via the '/Library/Developer/CommandLineTools/usr/bin/python3 -m pip install --upgrade pip' command.
Note: you may need to restart the kernel to use updated packages.


### New try

In [24]:
from Todd import (
    ScorerType, 
    MahalanobisScorer
)

In [21]:
from toddbenchmark.utils_classification import prepare_detectors
from toddbenchmark.classification_datasets import prep_dataset

In [22]:
prep_dataset("sst2",config=)

TypeError: prep_dataset() missing 2 required positional arguments: 'config' and 'tokenizer'